In [28]:
%matplotlib inline
import matplotlib.pyplot as plt
import IPython.display as ipd

import os
import json
import math
import torch
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader

import commons
import utils
from data_utils import TextAudioSpeakerLoader, TextAudioSpeakerCollate
from models import SynthesizerTrn
from text.symbols import symbols
from text import text_to_sequence

from scipy.io.wavfile import write
import numpy as np


def get_text(text, hps):
    text_norm = text_to_sequence(text, hps.data.text_cleaners)
    if hps.data.add_blank:
        text_norm = commons.intersperse(text_norm, 0)
    text_norm = torch.LongTensor(text_norm)
    return text_norm

DEBUG:matplotlib.pyplot:Loaded backend module://matplotlib_inline.backend_inline version unknown.


In [29]:
hps = utils.get_hparams_from_file("./configs/vtubers.json")

In [80]:
net_g = SynthesizerTrn(
    len(symbols),
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    n_speakers=hps.data.n_speakers,
    **hps.model)
_ = net_g.eval()

_ = utils.load_checkpoint("logs/vtubers/G_26800.pth", net_g, None)

INFO:root:Loaded checkpoint 'logs/vtubers/G_26800.pth' (iteration 127)
Loaded checkpoint 'logs/vtubers/G_26800.pth' (iteration 127) 


In [81]:
all_emotions = np.load("all_emotions.npy")
emotion_dict = {
    "小声": 2077,
    "激动": 111,
    "平静1": 434,
    "平静2": 3554
}
import random
def tts(txt, emotion):
    stn_tst = get_text(txt, hps)
    with torch.no_grad():
        x_tst = stn_tst.unsqueeze(0)
        x_tst_lengths = torch.LongTensor([stn_tst.size(0)])
        sid = torch.LongTensor([0])
        if type(emotion) ==int:
            emo = torch.FloatTensor(all_emotions[emotion]).unsqueeze(0)
        elif emotion == "random":
            emo = torch.randn([1,1024])
        elif emotion == "random_sample":
            randint = random.randint(0, all_emotions.shape[0])
            emo = torch.FloatTensor(all_emotions[randint]).unsqueeze(0)
            print(randint)
        elif emotion.endswith("wav"):
            import emotion_extract
            emo = torch.FloatTensor(emotion_extract.extract_wav(emotion))
        else:
            emo = torch.FloatTensor(all_emotions[emotion_dict[emotion]]).unsqueeze(0)

        audio = net_g.infer(x_tst, x_tst_lengths, sid=sid, noise_scale=0.667, noise_scale_w=0.8, length_scale=1, emo=emo)[0][0,0].data.float().numpy()
    ipd.display(ipd.Audio(audio, rate=hps.data.sampling_rate, normalize=False))

In [90]:
txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
tts(txt, emotion="小声")
tts(txt, emotion="激动")
tts(txt, emotion="平静1")
tts(txt, emotion="平静2")


In [83]:
txt = "こんにちは。私わあやちねねです。"
tts(txt, emotion="小声")
tts(txt, emotion="激动")
tts(txt, emotion="平静1")
# tts(txt, emotion="nen113_082.wav")

In [84]:
txt = "授業中に出したら、学校生活終わるなり。"
tts(txt, emotion="小声")
tts(txt, emotion="激动")
tts(txt, emotion="平静1")
tts(txt, emotion="平静2")

In [85]:
# 随机选取使用训练数据中某一条数据的情感
# 随机抽取的情感id可以用于使用该情感合成其他句子
txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')

1451


804


1826


3488


1749


4254


In [86]:
# 指定情感id合成，即上一步中的id
txt = "こんにちは。私わあやちねねです。"
tts(txt, emotion=4254)

In [93]:
txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
tts(txt, emotion="dataset/nene/nen112_107.wav")

### Voice Conversion

In [ ]:
dataset = TextAudioSpeakerLoader(hps.data.validation_files, hps.data)
collate_fn = TextAudioSpeakerCollate()
loader = DataLoader(dataset, num_workers=8, shuffle=False,
    batch_size=1, pin_memory=True,
    drop_last=True, collate_fn=collate_fn)
data_list = list(loader)

In [ ]:
with torch.no_grad():
    x, x_lengths, spec, spec_lengths, y, y_lengths, sid_src = [x.cuda() for x in data_list[0]]
    sid_tgt1 = torch.LongTensor([1]).cuda()
    sid_tgt2 = torch.LongTensor([2]).cuda()
    sid_tgt3 = torch.LongTensor([4]).cuda()
    audio1 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt1)[0][0,0].data.cpu().float().numpy()
    audio2 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt2)[0][0,0].data.cpu().float().numpy()
    audio3 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt3)[0][0,0].data.cpu().float().numpy()
print("Original SID: %d" % sid_src.item())
ipd.display(ipd.Audio(y[0].cpu().numpy(), rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt1.item())
ipd.display(ipd.Audio(audio1, rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt2.item())
ipd.display(ipd.Audio(audio2, rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt3.item())
ipd.display(ipd.Audio(audio3, rate=hps.data.sampling_rate, normalize=False))

In [5]:
all_emo = []
import os
for npyname in sorted(os.listdir("dataset/nene/")):
    if npyname.endswith("emo.npy"):
        all_emo.append(np.load(f"dataset/nene/{npyname}").reshape([1,-1]))
all_emotions = np.concatenate(all_emo, axis=0)

In [30]:
np.save("all_emotions.npy", all_emotions)

In [10]:
all_emo = []
wav_to_id = {}
import os
idx = 0
for npyname in sorted(os.listdir("dataset/nene/")):
    if npyname.endswith("emo.npy"):
        wav_to_id[npyname.replace(".emo.npy", "")] = idx
        idx +=1
        all_emo.append(np.load(f"dataset/nene/{npyname}").reshape([1,-1]))
all_emotions = np.concatenate(all_emo, axis=0)

In [15]:
wav_to_id["nen113_082.wav"]

3554

In [14]:
txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
tts(txt, emotion=434)
tts(txt, emotion="dataset/nene/nen005_110.wav")

In [1]:
import emotion_extract

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


Moving 0 files to the new cache system


0it [00:00, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [3]:
emotion_extract.extract_wav("dataset/nene/nen104_220.wav").shape

/home/ubuntu/vits-japanese-main/emotion_extract.py:106: FutureWarning: Pass sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  wav, sr = librosa.load(path, 16000)


(1, 1024)